How to test:
1. Run data_processing.ipynb -> It'll create a folder name data with a csv file per company
2. Run all in this file, if you want to test data you run the only last cell

In [3]:
import os
import torch
import torch.nn as nn
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
import torch.optim as optim
from tqdm import tqdm
from sklearn.preprocessing import MinMaxScaler
from torch.utils.data import DataLoader, TensorDataset
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score

FEATURE_COLUMNS = [
    "year", "month", "intrinsic_value", "stock_exret", "stock_ticker", "comp_name", "be_me", "ni_me", "fcf_me",
    "betadown_252d", "ni_ar1", "z_score", "ebit_sale", "at_turnover",
    "market_equity", "roic", "bvps", "prev_bvps", "bvps_change", "prev_at_turnover",
    "at_turnover_change", "prev_ni_me", "ni_me_change", "prev_fcf_me", "fcf_me_change",
    "sin_month", "cos_month"
] # 27 - 4 = 23
# ignore stock_ticker, comp_name, year, month, ni_me_change, fcf_me_change

SEQ_LENGTH = 12

COMPANY_DATA_FOLDER = "data_processing/outputs/by_ticker"
USE_CPU = True

In [4]:
def process_time_features(df):
    """ Remove `year`, and encode `month` cyclically """
    if "year" not in df.columns or "month" not in df.columns:
        raise KeyError("The dataset does not contain 'year' or 'month' columns.")

    df["sin_month"] = np.sin(2 * np.pi * df["month"] / 12)
    df["cos_month"] = np.cos(2 * np.pi * df["month"] / 12)
    return df
    # return df.drop(columns=["year", "month"])  # Remove original time columns

In [5]:
def normalize_features(df):
    # print(df)
    feature_columns = [col for col in df.columns if col not in ["year", "month", "stock_exret"]]

    # Identify non-numeric columns
    # non_numeric_cols = df[feature_columns].select_dtypes(exclude=[np.number]).columns.tolist()
    # if non_numeric_cols:
    #     print("Dropping non-numeric columns:", non_numeric_cols)
    #     df = df.drop(columns=non_numeric_cols)

    # Replace NaN and infinite values
    # df[feature_columns] = df[feature_columns].replace([np.inf, -np.inf], np.nan)  # Convert inf to NaN
    # # Check for infinity values
    # print("Has Inf values:\n", df.isin([np.inf, -np.inf]).sum())

    df[feature_columns] = df[feature_columns].fillna(0)  # Replace NaN with 0

    # Normalize using MinMaxScaler
    scaler = MinMaxScaler()
    df[feature_columns] = scaler.fit_transform(df[feature_columns])

    return df

In [6]:
def load_company_data(company):
    file_path = f"{COMPANY_DATA_FOLDER}/{company}.csv"

    if not os.path.exists(file_path):
        print(f"Skipping {company} (No data found)")
        return None, None

    df = pd.read_csv(file_path)

    df = df.fillna(0)  # Replace NaNs with 0
    
    df = df.drop(columns=["stock_ticker", "comp_name", "ni_me_change", "fcf_me_change",
    "prev_intrinsic_value","next_intrinsic_value","prev_stock_exret","next_stock_exret","prev_be_me",
    "next_be_me","prev_ni_me","next_ni_me","prev_fcf_me","next_fcf_me","prev_betadown_252d",
    "next_betadown_252d","prev_ni_ar1","next_ni_ar1","prev_z_score","next_z_score","prev_ebit_sale",
    "next_ebit_sale","prev_at_turnover","next_at_turnover","prev_market_equity","next_market_equity"
    ,"prev_bvps","next_bvps"
    ], errors="ignore")
    
    # Normalize feature columns (excluding year, month, and stock_exret)
    df = normalize_features(df)

    # print(df)

    # scaler_y = MinMaxScaler(feature_range=(-1, 1))
    # df["stock_exret"] = scaler_y.fit_transform(df[["stock_exret"]])

    
    if "year" not in df.columns or "month" not in df.columns:
        print(f"Skipping {company} (Missing 'year' or 'month' column)")
        return None, None

    # df = df.sort_values(by=["year", "month"]) # already sorted
    df_train = df[(df["year"] < 2023) | ((df["year"] == 2023) & (df["month"] < 12))].copy()
    df_test = df[(df["year"] == 2023) & (df["month"] == 12)].copy()

    df_train = process_time_features(df_train)
    df_test = process_time_features(df_test)

    return df_train, df_test

In [7]:
def create_lstm_sequences(df, seq_length, company_id):
    """
    Converts dataframe into LSTM sequences for training only.
    Uses a rolling window approach: each sequence consists of `seq_length` months,
    and the next month's value is the target.
    """
    X_train, Y_train, company_ids_train = [], [], []

    # df = df[df['year'] == 2022]
    # df = df[df['year'].isin([2022, 2023])]

    df = df.drop(columns=['year', 'month'])

    # print(df)

    df_values = df.values  # Convert DataFrame to numpy array
    num_samples = len(df_values)

    for i in range(num_samples - seq_length):
        x_seq = df_values[i:i + seq_length]  # Past `seq_length` months
        y_target = df_values[i + seq_length][0]  # Predict next month's `stock_exret`

        X_train.append(x_seq)
        Y_train.append(y_target)
        company_ids_train.append(company_id)

    return np.array(X_train), np.array(Y_train), np.array(company_ids_train)

In [8]:
class StockLSTM(nn.Module):
    def __init__(self, input_size, hidden_size, num_layers, output_size, num_companies, embedding_dim, dropout=0.2):
        super(StockLSTM, self).__init__()
        
        self.input_size = input_size

        # Company embedding layer
        self.embedding = nn.Embedding(num_companies, embedding_dim)

        # LSTM
        self.lstm = nn.LSTM(input_size + embedding_dim, hidden_size, num_layers, batch_first=True, dropout=dropout)

        # Dropout layer before the final output layer
        self.dropout = nn.Dropout(dropout)

        # Fully connected output layer
        self.fc = nn.Linear(hidden_size, output_size)

    def forward(self, x, company_ids):
        # Convert company IDs to embeddings
        company_embedding = self.embedding(company_ids).unsqueeze(1)  # (batch, 1, embedding_dim)
        company_embedding = company_embedding.expand(-1, x.shape[1], -1)  # Repeat across time steps

        # Concatenate embeddings with financial data
        x = torch.cat((x, company_embedding), dim=2)
        # print(f"Model forward input shape: {x.shape}")  # (batch, seq_length, input_size)

        # Pass through LSTM
        lstm_out, _ = self.lstm(x)

        # Use last time step's output for prediction
        output = self.fc(lstm_out[:, -1, :])

        return output

In [9]:
company_files = [f.split(".csv")[0] for f in os.listdir(COMPANY_DATA_FOLDER) if f.endswith(".csv")]  # 2501 companies
print(len(company_files))
company_to_id = {comp: idx for idx, comp in enumerate(company_files)}
print(company_to_id)

# Hyperparameters
num_epochs = 200
batch_size = 64

# Model parameters
feature_input_size = len(FEATURE_COLUMNS)  # This should match actual features before embedding
embedding_dim = 24  # sqrt(num_companies) 547 companies
input_size = 17  # feature_input_size(17) + embedding_dim(24) = 41

hidden_size = 64
num_layers = 2
output_size = 1
learning_rate = 0.001

547
{'LLY': 0, 'NVR': 1, 'NXST': 2, 'ROK': 3, 'AMZN': 4, 'RHI': 5, 'EHC': 6, 'PM': 7, 'SO': 8, 'UNH': 9, 'MSA': 10, 'DHR': 11, 'QLYS': 12, 'HPQ': 13, 'COF': 14, 'BIO': 15, 'LPLA': 16, 'PKG': 17, 'FLS': 18, 'WMB': 19, 'MIDD': 20, 'SEIC': 21, 'REGN': 22, 'BFAM': 23, 'AN': 24, 'IEX': 25, 'CMG': 26, 'LNC': 27, 'MSFT': 28, 'GD': 29, 'XYL': 30, 'UNM': 31, 'ASH': 32, 'GIS': 33, 'CDNS': 34, 'BRO': 35, 'FIVE': 36, 'MMC': 37, 'ROL': 38, 'VRTX': 39, 'AMG': 40, 'CL': 41, 'DXCM': 42, 'TTD': 43, 'DXC': 44, 'MELI': 45, 'HUN': 46, 'LEN': 47, 'TTC': 48, 'LFUS': 49, 'DOV': 50, 'LYV': 51, 'GDDY': 52, 'K': 53, 'PFGC': 54, 'WAT': 55, 'EXEL': 56, 'SF': 57, 'NDSN': 58, 'ULTA': 59, 'SLGN': 60, 'GPK': 61, 'WRB': 62, 'MA': 63, 'AOS': 64, 'RJF': 65, 'HIG': 66, 'ROST': 67, 'AMGN': 68, 'CTSH': 69, 'UAL': 70, 'ALK': 71, 'ADM': 72, 'LW': 73, 'IONS': 74, 'BF.B': 75, 'PFE': 76, 'PCTY': 77, 'FAST': 78, 'CSX': 79, 'EME': 80, 'WEC': 81, 'TOL': 82, 'AMAT': 83, 'WU': 84, 'TFX': 85, 'KNX': 86, 'AMP': 87, 'CW': 88, 'INTC': 8

In [10]:
# Combine data from all companies
all_X_train = []
all_Y_train = []
all_company_ids = []

t = tqdm(company_files)
for company in t:
    company_id = company_to_id[company]
    t.set_description_str(f"{company_id}: {company}")

    df_train, df_test = load_company_data(company)

    if df_train is None:
        continue

    #  intrinsic_value  stock_exret     be_me     ni_me    fcf_me
    #  betadown_252d    ni_ar1   z_score  ebit_sale  at_turnover  market_equity
    #  roic          bvps  bvps_change  at_turnover_change  sin_month  cos_month (17 columns)


    X_train_tensor, Y_train_tensor, company_train_tensor = create_lstm_sequences(df_train, 5, company_id)

    all_X_train.append(torch.tensor(X_train_tensor, dtype=torch.float32))
    all_Y_train.append(torch.tensor(Y_train_tensor, dtype=torch.float32).unsqueeze(1))
    all_company_ids.append(torch.tensor(company_train_tensor, dtype=torch.long))

546: PEG: 100%|██████████| 547/547 [00:04<00:00, 123.92it/s]  


In [12]:
if torch.cuda.is_available() and not USE_CPU:
    device = torch.device("cuda")
    print("CUDA enabled, on:", torch.cuda.get_device_name(device))
else:
    device = "cpu"
    print("--- USING CPU! ---")

--- USING CPU! ---


In [13]:
model = StockLSTM(input_size, hidden_size, num_layers, output_size, len(company_files), embedding_dim, dropout=0.2).to(device)

# criterion = nn.MSELoss()
criterion = nn.MSELoss()
optimizer = torch.optim.Adam(model.parameters(), lr=learning_rate)

# Concatenate all data
X_train_tensor = torch.cat(all_X_train, dim=0)
Y_train_tensor = torch.cat(all_Y_train, dim=0)
company_train_tensor = torch.cat(all_company_ids, dim=0)

# Create DataLoader
train_dataset = TensorDataset(X_train_tensor, company_train_tensor, Y_train_tensor)
train_dataloader = DataLoader(train_dataset, batch_size=batch_size, shuffle=True)

# Training
train_losses = []

for epoch in range(num_epochs):
    model.train()
    total_loss = 0

    for batch_X, batch_company, batch_Y in train_dataloader:
        batch_X, batch_company, batch_Y = batch_X.to(device), batch_company.to(device), batch_Y.to(device)

        optimizer.zero_grad()
        predictions = model(batch_X, batch_company).squeeze()
        loss = criterion(predictions, batch_Y)

        loss.backward()
        optimizer.step()

        total_loss += loss.item()

    avg_loss = total_loss / len(train_dataloader)
    train_losses.append(avg_loss)
    print(f"Epoch {epoch+1}/{num_epochs}, Train Loss: {avg_loss:.6f}")

# Plot Loss Curve
plt.figure(figsize=(8, 5))
plt.plot(range(1, num_epochs + 1), train_losses, marker='o', linestyle='-')
plt.xlabel("Epoch")
plt.ylabel("Training Loss")
plt.title("Training Loss Over Epochs")
plt.grid(True)
plt.show()


/home/jdtech/APS360/LSTM-Stock-Portfolio-Curation/.venv/lib/python3.12/site-packages/torch/nn/modules/loss.py:610: UserWarning: Using a target size (torch.Size([64, 1])) that is different to the input size (torch.Size([64])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)
/home/jdtech/APS360/LSTM-Stock-Portfolio-Curation/.venv/lib/python3.12/site-packages/torch/nn/modules/loss.py:610: UserWarning: Using a target size (torch.Size([38, 1])) that is different to the input size (torch.Size([38])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch 1/200, Train Loss: 0.071995
Epoch 2/200, Train Loss: 0.071118
Epoch 3/200, Train Loss: 0.071070
Epoch 4/200, Train Loss: 0.071067
Epoch 5/200, Train Loss: 0.071048
Epoch 6/200, Train Loss: 0.071042
Epoch 7/200, Train Loss: 0.071032
Epoch 8/200, Train Loss: 0.071030
Epoch 9/200, Train Loss: 0.071015
Epoch 10/200, Train Loss: 0.070986
Epoch 11/200, Train Loss: 0.070977
Epoch 12/200, Train Loss: 0.070995
Epoch 13/200, Train Loss: 0.071014
Epoch 14/200, Train Loss: 0.070966
Epoch 15/200, Train Loss: 0.070976
Epoch 16/200, Train Loss: 0.070983
Epoch 17/200, Train Loss: 0.070969
Epoch 18/200, Train Loss: 0.070969
Epoch 19/200, Train Loss: 0.070962
Epoch 20/200, Train Loss: 0.070972
Epoch 21/200, Train Loss: 0.070972
Epoch 22/200, Train Loss: 0.070962
Epoch 23/200, Train Loss: 0.070959
Epoch 24/200, Train Loss: 0.070968
Epoch 25/200, Train Loss: 0.070969
Epoch 26/200, Train Loss: 0.070973
Epoch 27/200, Train Loss: 0.070954
Epoch 28/200, Train Loss: 0.070979
Epoch 29/200, Train Loss: 0.0

KeyboardInterrupt: 

In [ ]:
# torch.save(model.state_dict(), "trained_stock_lstm.pth")
# print("\nModel saved!")

To test one company

In [ ]:
# CSCO
# Testing (Predict Dec 2023 & Compare to Actual)

test_company = input("\nEnter company name for testing: ")
df_train, df_test = load_company_data(test_company)
# input above
#  intrinsic_value  stock_exret     be_me     ni_me    fcf_me
#  betadown_252d    ni_ar1   z_score  ebit_sale  at_turnover  market_equity
#  roic          bvps  bvps_change  at_turnover_change  sin_month  cos_month (17 columns)

print(df_test)

# df_test is already processed because of load_company_data

if df_test is None or df_test.empty:
    print(f" No test data available for {test_company}.")
else:
    latest_financials = df_test.iloc[-1].to_dict()

    input_df = pd.DataFrame([latest_financials], columns=FEATURE_COLUMNS)

    input_df = input_df.drop(columns=["year", "month", "stock_ticker", "comp_name", "ni_me_change", "fcf_me_change",
    "prev_intrinsic_value","next_intrinsic_value","prev_stock_exret","next_stock_exret","prev_be_me",
    "next_be_me","prev_ni_me","next_ni_me","prev_fcf_me","next_fcf_me","prev_betadown_252d",
    "next_betadown_252d","prev_ni_ar1","next_ni_ar1","prev_z_score","next_z_score","prev_ebit_sale",
    "next_ebit_sale","prev_at_turnover","next_at_turnover","prev_market_equity","next_market_equity"
    ,"prev_bvps","next_bvps"
    ], errors="ignore")
    
    input_df = input_df.fillna(0)  # in case
    # input_df = normalize_features(input_df)
    print(input_df)
    
    input_tensor = torch.tensor(input_df.values, dtype=torch.float32).unsqueeze(0).to(device)

    print(input_tensor.shape) # torch.Size([1, 1, 19])
    
    test_company_id = torch.tensor([company_to_id[test_company]], dtype=torch.long).to(device)
    
    model.eval()
    with torch.no_grad():
        predicted_return = model(input_tensor, test_company_id).item()

    actual_return = df_test["stock_exret"].values[0]

    print(f"\nPredicted: {predicted_return:.4f} | Actual: {actual_return:.4f}")

     year  month  intrinsic_value  stock_exret     be_me     ni_me    fcf_me  \
0    2000      1     68860.120574     0.031587  0.153421  0.028945  0.004884   
1    2000      2     59293.871381    -0.096405  0.151659  0.024250  0.003750   
2    2000      3     59293.871381     0.030155  0.168021  0.026866  0.004154   
3    2000      4     59293.871381    -0.007808  0.161507  0.025825  0.003993   
4    2000      5     76916.656154     0.073069  0.294872  0.029259  0.015403   
..    ...    ...              ...          ...       ...       ...       ...   
271  2023      8    623435.020620     0.040819  0.511752  0.142284  0.134793   
272  2023      9    623435.020620     0.053169  0.498478  0.138593  0.131296   
273  2023     10    623435.020620    -0.104462  0.471388  0.131061  0.124161   
274  2023     11    492488.903600    -0.024806  0.530439  0.123297  0.110471   
275  2023     12    492488.903600    -0.031164  0.540601  0.125659  0.112588   

     betadown_252d    ni_ar1   z_score 

To test on multiple companies and find average (compare to baseline model)

In [11]:
# company files
company_files = [f.split(".csv")[0] for f in os.listdir("data") if f.endswith(".csv")]  # 2501 companies
company_to_id = {comp: idx for idx, comp in enumerate(company_files)}

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

model = StockLSTM(input_size, hidden_size, num_layers, output_size, len(company_files), embedding_dim).to(device)
model.load_state_dict(torch.load("trained_stock_lstm.pth", map_location=device))

# Collect test data across all companies
all_X_test = []
all_Y_test = []
all_company_ids_test = []

for test_company in company_files:
    company_id = company_to_id[test_company]
    
    df_train, df_test = load_company_data(test_company)    

    if df_test is None or df_test.empty:
        print(f"No test data available for {test_company}.")
        continue  # Skip if no test data

    # Extract latest financial data (last row)
    latest_financials = df_test.iloc[-1].to_dict()
    
    # Select only relevant features
    input_df = pd.DataFrame([latest_financials], columns=FEATURE_COLUMNS)

    input_df = input_df.drop(columns=["year", "month", "stock_ticker", "comp_name", "ni_me_change", "fcf_me_change",
        "prev_intrinsic_value", "next_intrinsic_value", "prev_stock_exret", "next_stock_exret", "prev_be_me",
        "next_be_me", "prev_ni_me", "next_ni_me", "prev_fcf_me", "next_fcf_me", "prev_betadown_252d",
        "next_betadown_252d", "prev_ni_ar1", "next_ni_ar1", "prev_z_score", "next_z_score", "prev_ebit_sale",
        "next_ebit_sale", "prev_at_turnover", "next_at_turnover", "prev_market_equity", "next_market_equity",
        "prev_bvps", "next_bvps"
    ], errors="ignore")

    # Fill NaN values
    input_df = input_df.fillna(0)

    # Convert to tensor
    input_tensor = torch.tensor(input_df.values, dtype=torch.float32).unsqueeze(0)  # Shape: (1, 1, num_features)

    # Store data for batch processing
    all_X_test.append(input_tensor)
    all_Y_test.append(torch.tensor(df_test["stock_exret"].values[-1], dtype=torch.float32).unsqueeze(0))
    all_company_ids_test.append(torch.tensor([company_id], dtype=torch.long))

# Combine into batch tensors
X_test_tensor = torch.cat(all_X_test, dim=0).to(device)  # Shape: (num_samples, 1, num_features)
Y_test_tensor = torch.cat(all_Y_test, dim=0).to(device)  # Shape: (num_samples, 1)
company_test_tensor = torch.cat(all_company_ids_test, dim=0).to(device)  # Shape: (num_samples,)

# Evaluate Model on Test Data
model.eval()
all_preds = []

with torch.no_grad():
    predictions = model(X_test_tensor, company_test_tensor).squeeze()
    all_preds = predictions.cpu().numpy()
    all_targets = Y_test_tensor.cpu().numpy()

# Compute Test Metrics
test_loss = criterion(predictions, Y_test_tensor).item()
r2 = r2_score(all_targets, all_preds)
mape = np.mean(np.abs((all_targets - all_preds) / (all_targets + 1e-8))) * 100  # Avoid division by zero

print(f"\nTest Loss: {test_loss:.6f}")
print(f"Test R² Score: {r2:.4f}")
print(f"Test MAPE: {mape:.2f}%")


     year  month  intrinsic_value  stock_exret     be_me     ni_me    fcf_me  \
0    2000      1     23717.660301     0.018070  0.033325  0.005981  0.010998   
1    2000      2     23717.660301     0.202892  0.032603  0.005852  0.010760   
2    2000      3     21657.871605     0.165040  0.033149  0.004461  0.009510   
3    2000      4     21657.871605    -0.107874  0.028339  0.003814  0.008130   
4    2000      5     21657.871605    -0.183724  0.029532  0.003974  0.008472   
..    ...    ...              ...          ...       ...       ...       ...   
274  2023      8    102622.883210     0.097537  0.196007  0.053413  0.073008   
275  2023      9    103991.324910    -0.066898  0.181380  0.049188  0.072226   
276  2023     10    103991.324910    -0.027765  0.194023  0.052617  0.077261   
277  2023     11    103991.324910    -0.076336  0.200380  0.054341  0.079792   
278  2023     12    119716.330640     0.039933  0.225926  0.064159  0.096836   

     betadown_252d    ni_ar1    z_score